In [ ]:
import os
import sys
import logging
import pickle
import re
import numpy as np
import pandas as pd
#import matplotlib.pyplot as plt  # Removed for no plots
#import matplotlib.patches as patches
#import matplotlib as mpl
#import matplotlib.font_manager as fm
#import seaborn as sns
from datetime import datetime
import traceback
import warnings
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
# Sklearn & Models
from sklearn.model_selection import KFold, cross_val_score
from sklearn.feature_selection import RFECV
from sklearn.ensemble import (RandomForestRegressor, GradientBoostingRegressor,
                              AdaBoostRegressor, ExtraTreesRegressor)
from sklearn.linear_model import ElasticNet
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from scipy.stats import pearsonr
from sklearn.svm import SVR
# Boosters
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import HistGradientBoostingRegressor
# Optimization & Explanation
import optuna
import shap
# ------------------------------------------------------------------------------
# 0. LIVE LOGGING SETUP
# ------------------------------------------------------------------------------
warnings.filterwarnings('ignore')
log_filename = f"pipeline_log_{datetime.now().strftime('%Y%m%d_%H%M%S')}.txt"
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s | %(levelname)s | %(message)s',
    handlers=[
        logging.FileHandler(log_filename, mode='a', encoding='utf-8'),
        logging.StreamHandler(sys.stdout)
    ]
)

# ------------------------------------------------------------------------------
# 1. MASTER CONFIGURATION
# ------------------------------------------------------------------------------
np.random.seed(42)
MAIN_ROOT_DIR = "FINAL_RESULTS"
REMOVE_OUTLIERS = True
# --- RUNTIME CONTROLS ---
N_TRIALS_OPTUNA = 2000
base_feature_cols = [
    'Z_A', 'Z_B', 'IE_A', 'IE_B', 'EN_A', 'EN_B', 'EA_A', 'EA_B',
    'AD_A', 'AD_B', 'IR_A', 'IR_B', 'MP_A', 'MP_B', 'BP_A', 'BP_B',
    'HE_A', 'HE_B', 'HF_A', 'HF_B', 'Tf', 'Of', 'τ', 'T'
]
# RFE Settings
rfe_params = {} 
TARGETS = [
    {"col": "σ", "name": "Electrical Conductivity σ(S_cm)", "bounds": (0, 15000)},
    {"col": "κ", "name": "Thermal Conductivity κ(W_m-K)", "bounds": (0.00, 5)},
    {"col": "S", "name": "Seebeck Coefficient S(μV_K)", "bounds": (-1000, 1000)},
    {"col": "zT", "name": "Figure of Merit zT", "bounds": (0.00, 0.45)}
]
# ------------------------------------------------------------------------------
# 2. Model Instances
# ------------------------------------------------------------------------------
def get_fresh_models():
    return {
        'RandomForest': RandomForestRegressor(random_state=42, n_jobs=-1),
        'GradientBoost': GradientBoostingRegressor(random_state=42),
        'AdaBoost': AdaBoostRegressor(random_state=42),
        'ExtraTrees': ExtraTreesRegressor(random_state=42),
        'XGBoost': XGBRegressor(random_state=42, objective='reg:squarederror',n_jobs=1),
        'LightGBM': LGBMRegressor(random_state=42, verbose=-1, n_jobs=1, force_col_wise=True),
        'CatBoost': CatBoostRegressor(random_state=42, verbose=0, allow_writing_files=False, thread_count=1),
        "HistGradientBoosting": HistGradientBoostingRegressor(random_state=42, loss="squared_error",)
    }
# ------------------------------------------------------------------------------
# 3.  Hyperparameter Spaces 
# ------------------------------------------------------------------------------
optuna_param_spaces = {
    "RandomForest": {
        "n_estimators": (100, 2000, "int"), 
        "max_depth": (5, 50, "int"),
        "min_samples_split": (2, 15, "int"), 
        "min_samples_leaf": (1, 10, "int"),
        "max_features": (["sqrt", "log2"], "categorical")
    },
    "GradientBoost": {
        "n_estimators": (100, 2000, "int"), 
        "learning_rate": (1e-4, 0.5, "float_log"),
        "max_depth": (3, 15, "int"), 
        "subsample": (0.5, 1.0, "float"),
        "min_samples_split": (2, 20, "int")
    },
    "AdaBoost": {
        "n_estimators": (50, 2000, "int"), 
        "learning_rate": (1e-4, 2.0, "float_log"),
        "loss": (["linear", "square", "exponential"], "categorical")
    },
    "ExtraTrees": {
        "n_estimators": (100, 2000, "int"), 
        "max_depth": (5, 50, "int"),
        "min_samples_split": (2, 15, "int"), 
        "min_samples_leaf": (1, 10, "int"),
        "max_features": (["sqrt", "log2"], "categorical")
    },
     "HistGradientBoosting": {
        "max_iter": (200, 200, "int"),
        "learning_rate": (1e-3, 0.2, "float_log"),
        "max_depth": (3, 15, "int"),
        "min_samples_leaf": (10, 100, "int"),
        "l2_regularization": (1e-6, 1.0, "float_log")
    },
   
    "XGBoost": {
        "n_estimators": (100, 2000, "int"), 
        "learning_rate": (1e-4, 0.5, "float_log"),
        "max_depth": (3, 15, "int"), 
        "subsample": (0.5, 1.0, "float"),
        "colsample_bytree": (0.5, 1.0, "float"), 
        "reg_alpha": (1e-3, 10.0, "float_log"),
        "reg_lambda": (1e-3, 10.0, "float_log"), 
        "min_child_weight": (1, 10, "int")
    },
    "LightGBM": {
        "n_estimators": (100, 2000, "int"),
        "learning_rate": (1e-3, 0.3, "float_log"),
        "num_leaves": (5, 40, "int"),
        "max_depth": (3, 10, "int"),
        "min_child_samples": (3, 20, "int"),
        "reg_alpha": (1e-3, 1.0, "float_log"),
        "reg_lambda": (1e-3, 1.0, "float_log")
    },
    "CatBoost": {
        "iterations": (200, 2000, "int"), 
        "learning_rate": (1e-4, 0.5, "float_log"),
        "depth": (4, 12, "int"), 
        "l2_leaf_reg": (1e-3, 10.0, "float_log"),
        "subsample": (0.5, 1.0, "float"), 
        "random_strength": (0.0, 10.0, "float")
    }
}
# ------------------------------------------------------------------------------
# 4. Preprocessing & Visualization
# ------------------------------------------------------------------------------
def load_and_preprocess_data(csv_file):
    logging.info(f"Loading data from {csv_file}...")
    df = pd.read_csv(csv_file)
    df.columns = [re.sub(r'[^\w]', '_', col) for col in df.columns]
    return df
def feature_engineering(df, feature_cols, target_column):
    df_new = df.copy()
    new_feature_cols = feature_cols.copy()
    return df_new, new_feature_cols
def remove_outliers_hard_range(df, column, min_val, max_val):
    df_clean = df.copy()
    initial_count = df_clean.shape[0]
    df_clean = df_clean[(df_clean[column] >= min_val) & (df_clean[column] <= max_val)]
    dropped_count = initial_count - df_clean.shape[0]
    logging.info(f"📉 Outlier Removal ({column}): Dropped {dropped_count} rows.")
    return df_clean
def filter_highly_correlated_features(df, feature_cols, target_col, threshold=0.85):
    all_cols = feature_cols + [target_col]
    corr_matrix = df[all_cols].corr().abs()
    upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(bool))
    to_drop = [col for col in upper.columns if any(upper[col] > threshold) and col in feature_cols]
    logging.info(f"Dropping {len(to_drop)} highly correlated input features: {to_drop}")
    filtered_features = [col for col in feature_cols if col not in to_drop]
    return filtered_features, corr_matrix.loc[filtered_features, all_cols]
def perform_rfe(X, y, params, output_dir):
    logging.info("Starting RFE Feature Selection...")
    os.makedirs(output_dir, exist_ok=True)
   
    model = ExtraTreesRegressor(random_state=42, **params)
    selector = RFECV(estimator=model, step=1, cv=KFold(5, shuffle=True, random_state=42),
                     scoring='r2', n_jobs=-1, min_features_to_select=1)
    selector.fit(X, y)
    selected_features = X.columns[selector.support_].tolist()
    logging.info(f"✅ RFE Selected {len(selected_features)} features.")
   
    # --- EXPORT RFE SELECTION DETAILS ---
    rfe_details = pd.DataFrame({
        'Feature_Name': X.columns,
        'Is_Selected': selector.support_,
        'Rank': selector.ranking_
    }).sort_values('Rank')
    rfe_details.to_excel(f"{output_dir}/RFE_Feature_Selection_Details.xlsx", index=False)
    
    # --- EXPORT RFE PLOT DATA ---
    scores = selector.cv_results_['mean_test_score']
    n_features_range = range(1, len(scores) + 1)
    rfe_plot_data = pd.DataFrame({
        'Num_Features': n_features_range,
        'CV_R2_Score': scores
    })
    rfe_plot_data.to_excel(f"{output_dir}/RFE_Plot_Data.xlsx", index=False)
    
    return selected_features, selector
    
# ------------------------------------------------------------------------------
# 55. Optimization, Evaluation & CONVERGENCE ANALYSIS
# ------------------------------------------------------------------------------
def optuna_objective(trial, model_instance, param_space, X, y):
    params = {}
    for key, values in param_space.items():
        if len(values) == 2 and values[1] == "categorical":
            params[key] = trial.suggest_categorical(key, values[0])
        elif len(values) == 3:
            if values[2] == "int": params[key] = trial.suggest_int(key, values[0], values[1])
            elif values[2] == "float": params[key] = trial.suggest_float(key, values[0], values[1])
            elif values[2] == "float_log": params[key] = trial.suggest_float(key, values[0], values[1], log=True)
    if type(model_instance).__name__ == "CatBoostRegressor":
        model = CatBoostRegressor(**params, verbose=0, random_state=42, allow_writing_files=False)
    else:
        model = model_instance.set_params(**params)
       
    kf = KFold(5, shuffle=True, random_state=42)
    scores = cross_val_score(model, X, y, cv=kf, scoring='r2', n_jobs=-1)
    return scores.mean()

def tune_with_optuna(model_name, model, param_space, X, y, output_dir, n_trials=N_TRIALS_OPTUNA):
    db_name = f"optuna_{model_name}.db"
    os.makedirs(output_dir, exist_ok=True)
    db_path = os.path.join(output_dir, db_name).replace("\\", "/")
    storage_url = f"sqlite:///{db_path}"
   
    study = optuna.create_study(direction="maximize", storage=storage_url, study_name=model_name, load_if_exists=True)
   
    logging.info(f" > Optuna: {len(study.trials)}/{n_trials} trials previously done.")
    if len(study.trials) < n_trials:
        study.optimize(lambda t: optuna_objective(t, model, param_space, X, y), n_trials=(n_trials - len(study.trials)))
   
    hist = pd.DataFrame([{'Trial': t.number, 'Value': t.value, **t.params} for t in study.trials])
    hist.to_excel(f"{output_dir}/optuna_log_{model_name}.xlsx", index=False)
   
    return model.set_params(**study.best_params), study.best_params, study
def evaluate_model_cv(model, X, y, model_name, best_params, output_dir, target_label_clean):
    kf = KFold(5, shuffle=True, random_state=42)
    results = {'R2': [], 'MAE': [], 'RMSE': [], 'r': []}
    parity_rows = []
    for fold, (tr, te) in enumerate(kf.split(X), start=1):
        X_tr, X_te = X.iloc[tr], X.iloc[te]
        y_tr, y_te = y.iloc[tr], y.iloc[te]
        model.fit(X_tr, y_tr)
        pred_tr = model.predict(X_tr)
        pred_te = model.predict(X_te)
        results['R2'].append(r2_score(y_te, pred_te))
        results['MAE'].append(mean_absolute_error(y_te, pred_te))
        results['RMSE'].append(np.sqrt(mean_squared_error(y_te, pred_te)))
        results['r'].append(pearsonr(y_te, pred_te)[0])
        # ---- SAVE PARITY FOR ALL FOLDS (Train + Test) ----
        for a, p in zip(y_tr, pred_tr):
            parity_rows.append([fold, "Train", a, p])
        for a, p in zip(y_te, pred_te):
            parity_rows.append([fold, "Test", a, p])
    parity_df = pd.DataFrame(
        parity_rows,
        columns=["Fold", "Set", "Actual", "Predicted"]
    )
    parity_df.to_excel(
        f"{output_dir}/parity_all_folds_{model_name}.xlsx",
        index=False
    )
    return {
        'Model': model_name,
        'Best_Params': str(best_params),
        'R²_Mean': np.mean(results['R2']),
        'R²_Std': np.std(results['R2']),
        'MAE_Mean': np.mean(results['MAE']),
        'MAE_Std': np.std(results['MAE']),
        'RMSE_Mean': np.mean(results['RMSE']),
        'RMSE_Std': np.std(results['RMSE']),
        'r-value_Mean': np.mean(results['r']),
        'r-value_Std': np.std(results['r']),
        'parity_data': parity_df
    }

# Feature Aware Model Wrapper
class FeatureAwareModel:
    def __init__(self, model, feature_names, target_name=None):
        self.model = model
        self.feature_names = list(feature_names)
        self.target_name = target_name
    def predict(self, X): return self.model.predict(X[self.feature_names])
    def fit(self, X, y):
        self.model.fit(X[self.feature_names], y)
        return self
    def get_feature_names(self): return self.feature_names
def perform_shap_analysis(best_model, X, y, output_dir, target_label_clean):
    try:
        explainer = shap.TreeExplainer(best_model)
        shap_values = explainer.shap_values(X)
        
        # Export SHAP summary data (with feature values + SHAP values)
        summary_data_list = []
        for i, feature_name in enumerate(X.columns):
            temp_df = pd.DataFrame({
                'Feature_Name': feature_name,
                'Feature_Value': X[feature_name].values,
                'SHAP_Value': shap_values[:, i] if shap_values.ndim > 1 else shap_values
            })
            summary_data_list.append(temp_df)
        full_summary_df = pd.concat(summary_data_list, ignore_index=True)
        full_summary_df.to_excel(f'{output_dir}/shap_summary_data_with_values.xlsx', index=False)
        
        #  classic feature importance data
        feature_importance = np.abs(shap_values).mean(axis=0)
        importance_df = pd.DataFrame({
            'Feature_Name': X.columns,
            'Mean_Abs_SHAP': feature_importance
        }).sort_values('Mean_Abs_SHAP', ascending=False)
        importance_df.to_excel(f'{output_dir}/shap_feature_importance.xlsx', index=False)
        
        # Dependence data 
        dependence_data_list = []
        for i, feature_name in enumerate(X.columns):
            feature_data = X.iloc[:, i].values
            feature_shap = shap_values[:, i] if shap_values.ndim > 1 else shap_values
            temp_df = pd.DataFrame({
                'Feature_Name': feature_name,
                'Feature_Value': feature_data,
                'SHAP_Value': feature_shap,
                'Target_True_Value': y.values
            })
            dependence_data_list.append(temp_df)
        
        full_dependence_df = pd.concat(dependence_data_list, ignore_index=True) if dependence_data_list else pd.DataFrame()
        full_dependence_df.to_excel(f'{output_dir}/shap_dependence_all.xlsx', index=False)
        
        # Removed all actual plot calls
        return shap_values, full_summary_df, full_dependence_df
    except Exception as e:
        logging.warning(f"SHAP failed: {e}")
        return None, None, None
def export_all_data(corr_df, rfe_selector, results_list, shap_values, shap_summary_df, shap_dep_df, X_selected, output_path):
    logging.info(f"Exporting full results to {output_path}...")
    with pd.ExcelWriter(output_path, engine='openpyxl') as writer:
        if corr_df is not None and not corr_df.empty:
            corr_df.to_excel(writer, sheet_name='Feature_Correlation_Incl_Target')
        if rfe_selector:
            pd.DataFrame({
                "Num_Features": list(range(1, len(rfe_selector.cv_results_['mean_test_score']) + 1)),
                "CV_R2_Score": rfe_selector.cv_results_['mean_test_score']
            }).to_excel(writer, sheet_name='RFE_CV_Scores', index=False)
           
        for res in results_list:
            if 'parity_data' in res and res['parity_data'] is not None:
                pd.DataFrame(res['parity_data']).to_excel(writer, sheet_name=f'Parity_{res["Model"]}'[:31], index=False)
       
        if shap_values is not None:
            pd.DataFrame(shap_values, columns=X_selected.columns).to_excel(writer, sheet_name='SHAP_Values_Matrix', index=False)
       
        if shap_summary_df is not None and not shap_summary_df.empty:
            shap_summary_df.to_excel(writer, sheet_name='SHAP_Summary_With_Values', index=False)
       
        if shap_dep_df is not None and not shap_dep_df.empty:
            shap_dep_df.to_excel(writer, sheet_name='SHAP_Dependence_All', index=False)
    logging.info("Export complete.")
# ------------------------------------------------------------------------------
# 6. EXPERIMENT RUNNER
# ------------------------------------------------------------------------------
def run_experiment(method_name, models_dict, X, y, output_subdir, corr_df, rfe_selector, target_label_clean):
    logging.info(f"\n🚀 STARTING EXPERIMENT: {method_name.upper()}")
    os.makedirs(output_subdir, exist_ok=True)
    checkpoint_csv = f"{output_subdir}/checkpoint_metrics.csv"
   
    completed_results = []
    completed_model_names = []
   
    if os.path.exists(checkpoint_csv):
        try:
            completed_results = pd.read_csv(checkpoint_csv).to_dict('records')
            completed_model_names = [r['Model'] for r in completed_results]
            logging.info(f"🔄 Resuming... Found: {completed_model_names}")
        except: pass
    best_models_map = {}
    for model_name, model in models_dict.items():
        if model_name in completed_model_names:
            logging.info(f" ⏩ Skipping {model_name} (Done).")
            continue
        logging.info(f" ... Tuning {model_name} ...")
       
        try:
            optuna_study_ref = None
            best_model = model
            best_params = "Default"
            # === 1. BASIC RUN (NO TUNING) ===
            if method_name == "Basic":
                best_model = model # Use as is
                best_params = "Default"
            # === 2. OPTIMIZED RUN (OPTUNA) ===
            elif method_name == "Optimized":
                space = optuna_param_spaces.get(model_name, {})
                best_model, best_params, optuna_study_ref = tune_with_optuna(model_name, model, space, X, y, output_subdir)

            # Evaluate
            res = evaluate_model_cv(best_model, X, y, model_name, best_params, output_subdir, target_label_clean)
           
            # Checkpoint
            with open(f"{output_subdir}/parity_data_{model_name}.pkl", 'wb') as f: pickle.dump(res['parity_data'], f)
            with open(f"{output_subdir}/model_{model_name}.pkl", 'wb') as f: pickle.dump(best_model, f)
           
            res_no_parity = {k:v for k,v in res.items() if k != 'parity_data'}
            completed_results.append(res)
            best_models_map[model_name] = best_model
           
            pd.DataFrame([res_no_parity]).to_csv(checkpoint_csv, mode='a', header=not os.path.exists(checkpoint_csv), index=False)
            logging.info(f" ✅ Finished {model_name}")
        except Exception as e:
            logging.error(f" ❌ Failed {model_name}: {e}")
            traceback.print_exc()
    best_overall_score = -np.inf
    best_overall_model_name = ""
    best_overall_params = ""
    if completed_results:
        results_df = pd.DataFrame(completed_results).drop(columns=['parity_data'], errors='ignore')
        results_df.to_excel(f'{output_subdir}/evaluation_summary.xlsx', index=False)
        # Removed bar plots
        best_row = results_df.loc[results_df['R²_Mean'].idxmax()]
        best_overall_model_name = best_row['Model']
        best_overall_score = best_row['R²_Mean']
        best_overall_params = best_row['Best_Params']
       
        logging.info(f"🏆 Best Model ({method_name}): {best_overall_model_name}")
        # Final SHAP & Export
        if best_overall_model_name in best_models_map:
            final_model = best_models_map[best_overall_model_name]
            final_model.fit(X, y)
            shap_vals, shap_summary_df, shap_dep_df = perform_shap_analysis(final_model, X, y, output_subdir, target_label_clean)
           
            final_wrapped = FeatureAwareModel(final_model, X.columns.tolist(), target_label_clean)
           
            # --- 1. SAVE LOCAL COPY ---
            with open(f'{output_subdir}/FINAL_BEST_MODEL.pkl', 'wb') as f: pickle.dump(final_wrapped, f)
           
            # --- 2. SAVE GLOBAL COPY TO 'final_models' FOLDER (Only for Optimized) ---
            if method_name == "Optimized":
                final_models_dir = "final_models"
                os.makedirs(final_models_dir, exist_ok=True)
                safe_target = re.sub(r'[^\w\-]', '_', target_label_clean)
                save_path_global = f"{final_models_dir}/{safe_target}_{best_overall_model_name}.pkl"
                with open(save_path_global, 'wb') as f: pickle.dump(final_wrapped, f)
                logging.info(f"💾 Copied Final Model to: {save_path_global}")
            export_all_data(corr_df, rfe_selector, completed_results, shap_vals, shap_summary_df, shap_dep_df, X, f'{output_subdir}/FINAL_RESULTS.xlsx')
    return best_overall_score, best_overall_model_name, best_overall_params
# ------------------------------------------------------------------------------
# 77. Main Loop
# ------------------------------------------------------------------------------
def main():
    if not os.path.exists('data/final_data.csv'):
        logging.error("data/final_data.csv not found!")
        return
    for target_config in TARGETS:
        current_col = target_config["col"]
        current_name = target_config["name"]
        bounds = target_config["bounds"]
       
        safe_folder_name = re.sub(r'[^\w\-]', '_', current_name)
        target_output_dir = f"{MAIN_ROOT_DIR}/{safe_folder_name}"
       
        logging.info(f"\n\n{'#'*60}\nSTARTING PIPELINE FOR: {current_name}\n{'#'*60}")
       
        df = load_and_preprocess_data('final_data.csv')
        if current_col not in df.columns: continue
       
        # 1. Drop NaNs
        df = df.dropna(subset=[current_col])
        logging.info(f"📊 Data Shape after dropping NaNs: {df.shape}")
        # 2. Outlier Removal Tracking
        if REMOVE_OUTLIERS:
            logging.info(f"📊 Data Shape BEFORE Outlier Removal: {df.shape}")
            df = remove_outliers_hard_range(df, current_col, bounds[0], bounds[1])
            logging.info(f"📊 Data Shape AFTER Outlier Removal: {df.shape}")
       
        # 3. Save Processed Data
        os.makedirs(target_output_dir, exist_ok=True)
        processed_data_path = f"{target_output_dir}/processed_data_{safe_folder_name}.csv"
        df.to_csv(processed_data_path, index=False)
        logging.info(f"💾 Saved Processed Data to: {processed_data_path}")
        # 4. Feature Engineering
        df, engineered_features = feature_engineering(df, base_feature_cols, current_col)
        filtered_features, corr_df = filter_highly_correlated_features(df, engineered_features, current_col)
       
        common_dir = f"{target_output_dir}/00_Common_Analysis"
        os.makedirs(common_dir, exist_ok=True)

        # Save correlation matrix to Excel instead
        corr_df.to_excel(f"{common_dir}/pearson_correlation_incl_target.xlsx")
       
        X_full = df[filtered_features].fillna(df[filtered_features].mean())
        y_full = df[current_col]
       
        selected_features, rfe_selector = perform_rfe(X_full, y_full, rfe_params, common_dir)
        X_selected = X_full[selected_features]
        
        grand_results = []
       
        # --- RUN 1: BASIC (Default Params) ---
        s1, n1, p1 = run_experiment("Basic", get_fresh_models(), X_selected, y_full,
                                    f"{target_output_dir}/01_Basic_Default", corr_df, rfe_selector, current_name)
        grand_results.append({"Method": "Basic", "Best_Model": n1, "R2_Score": s1, "Params": p1})
        # --- RUN 2: OPTIMIZED (Optuna) ---
        s2, n2, p2 = run_experiment("Optimized", get_fresh_models(), X_selected, y_full,
                                    f"{target_output_dir}/02_Optimized_Optuna", corr_df, rfe_selector, current_name)
        grand_results.append({"Method": "Optimized", "Best_Model": n2, "R2_Score": s2, "Params": p2})
       
        grand_df = pd.DataFrame(grand_results).sort_values("R2_Score", ascending=False)
        print(grand_df)
        grand_df.to_excel(f"{target_output_dir}/GRAND_CHAMPION_SUMMARY.xlsx", index=False)
    logging.info("\n✅ ALL TARGETS PROCESSED SUCCESSFULLY.")
if __name__ == "__main__":
    main()

2025-12-26 23:23:16,326 | INFO | 

############################################################
STARTING PIPELINE FOR: Electrical Conductivity σ(S_cm)
############################################################
2025-12-26 23:23:16,326 | INFO | Loading data from final_data.csv...
ERROR! Session/line number was not unique in database. History logging moved to new session 179
2025-12-26 23:23:16,346 | INFO | 📊 Data Shape after dropping NaNs: (1680, 37)
2025-12-26 23:23:16,347 | INFO | 📊 Data Shape BEFORE Outlier Removal: (1680, 37)
2025-12-26 23:23:16,347 | INFO | 📉 Outlier Removal (σ): Dropped 38 rows.
2025-12-26 23:23:16,347 | INFO | 📊 Data Shape AFTER Outlier Removal: (1642, 37)
2025-12-26 23:23:16,393 | INFO | 💾 Saved Processed Data to: FINAL_RESULTS/Electrical_Conductivity_σ_S_cm_/processed_data_Electrical_Conductivity_σ_S_cm_.csv
2025-12-26 23:23:16,399 | INFO | Dropping 10 highly correlated input features: ['EA_B', 'AD_A', 'AD_B', 'BP_B', 'HE_A', 'HE_B', 'HF_B', 'Tf', 'Of', 'τ']
2

[I 2025-12-26 23:23:41,217] A new study created in RDB with name: RandomForest


2025-12-26 23:23:41,220 | INFO |  > Optuna: 0/2000 trials previously done.


[I 2025-12-26 23:23:41,537] Trial 0 finished with value: 0.7920300331225324 and parameters: {'n_estimators': 213, 'max_depth': 38, 'min_samples_split': 13, 'min_samples_leaf': 9, 'max_features': 'sqrt'}. Best is trial 0 with value: 0.7920300331225324.
[I 2025-12-26 23:23:42,888] Trial 1 finished with value: 0.7906503362067563 and parameters: {'n_estimators': 1223, 'max_depth': 24, 'min_samples_split': 14, 'min_samples_leaf': 9, 'max_features': 'log2'}. Best is trial 0 with value: 0.7920300331225324.
[I 2025-12-26 23:23:44,186] Trial 2 finished with value: 0.8166071354717686 and parameters: {'n_estimators': 1183, 'max_depth': 27, 'min_samples_split': 4, 'min_samples_leaf': 8, 'max_features': 'sqrt'}. Best is trial 2 with value: 0.8166071354717686.
[I 2025-12-26 23:23:46,172] Trial 3 finished with value: 0.869243134318008 and parameters: {'n_estimators': 1718, 'max_depth': 20, 'min_samples_split': 13, 'min_samples_leaf': 5, 'max_features': 'log2'}. Best is trial 3 with value: 0.869243134

2025-12-27 00:17:56,131 | INFO |  ✅ Finished RandomForest
2025-12-27 00:17:56,131 | INFO |  ... Tuning GradientBoost ...


...

[I 2025-12-27 12:23:04,382] Trial 0 finished with value: 0.9278152833507219 and parameters: {'max_iter': 200, 'learning_rate': 0.01736452129038293, 'max_depth': 15, 'min_samples_leaf': 10, 'l2_regularization': 0.44314739172619755}. Best is trial 0 with value: 0.9278152833507219.
[I 2025-12-27 12:23:04,595] Trial 1 finished with value: 0.6311423548166346 and parameters: {'max_iter': 200, 'learning_rate': 0.0037500693527241905, 'max_depth': 11, 'min_samples_leaf': 30, 'l2_regularization': 1.6625890072768762e-05}. Best is trial 0 with value: 0.9278152833507219.
[I 2025-12-27 12:23:04,713] Trial 2 finished with value: 0.5064442986414234 and parameters: {'max_iter': 200, 'learning_rate': 0.005494879662425687, 'max_depth': 3, 'min_samples_leaf': 95, 'l2_regularization': 0.00040473936970882767}. Best is trial 0 with value: 0.9278152833507219.
[I 2025-12-27 12:23:04,975] Trial 3 finished with value: 0.924507285691486 and parameters: {'max_iter': 200, 'learning_rate': 0.03622271040561679, 'max_

2025-12-27 18:35:31,734 | INFO |  ✅ Finished AdaBoost
2025-12-27 18:35:31,735 | INFO |  ... Tuning ExtraTrees ...


[I 2025-12-27 18:35:31,875] A new study created in RDB with name: ExtraTrees


2025-12-27 18:35:31,880 | INFO |  > Optuna: 0/2000 trials previously done.


[I 2025-12-27 18:35:32,779] Trial 0 finished with value: 0.8085359509951114 and parameters: {'n_estimators': 790, 'max_depth': 16, 'min_samples_split': 8, 'min_samples_leaf': 3, 'max_features': 'sqrt'}. Best is trial 0 with value: 0.8085359509951114.
[I 2025-12-27 18:35:34,267] Trial 1 finished with value: 0.6852306692289394 and parameters: {'n_estimators': 1565, 'max_depth': 16, 'min_samples_split': 13, 'min_samples_leaf': 8, 'max_features': 'log2'}. Best is trial 0 with value: 0.8085359509951114.
[I 2025-12-27 18:35:35,663] Trial 2 finished with value: 0.7757926350252433 and parameters: {'n_estimators': 1346, 'max_depth': 45, 'min_samples_split': 15, 'min_samples_leaf': 1, 'max_features': 'log2'}. Best is trial 0 with value: 0.8085359509951114.
[I 2025-12-27 18:35:37,348] Trial 3 finished with value: 0.8044949812452729 and parameters: {'n_estimators': 1691, 'max_depth': 34, 'min_samples_split': 12, 'min_samples_leaf': 1, 'max_features': 'sqrt'}. Best is trial 0 with value: 0.80853595